In [1]:
import warnings
warnings.filterwarnings(action='ignore')
import requests
import folium
# !pip install pandas # 파이썬 데이터 처리 라이브러리
import pandas as pd
from pandas.io.json import json_normalize # 파이썬 딕셔너리 타입의 데이터를 판다스 데이터프레임으로 변환한다.

# 전국 또는 특정 지역의 스타벅스 매장 위치 정보를 가져와서 지도위에 표시하기
requests로 스타벅스 매장의 위치 정보를 가져와서 딕셔너리 타입으로 변환한다.  
json_normalize() 함수로 json 타입의 데이터가 변환된 파이썬 딕셔너리를 판다스 데이터프레임으로 변환한다.  
folium 모듈을 사용해서 지도를 표시하고 지도위에 스타벅스 매장 위치를 마커로 표시한다.

In [2]:
# 서울 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '01',
    'p_gugun_cd': '',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
print(type(starbucks))
print(starbucks)

<class 'dict'>
{'list': [{'seq': 0, 'sido_cd': None, 'sido_nm': None, 'gugun_cd': None, 'gugun_nm': None, 'code_order': None, 'view_yn': None, 'store_num': None, 'sido': None, 'gugun': None, 'address': None, 'new_img_nm': None, 'p_pro_seq': 0, 'p_view_yn': None, 'p_sido_cd': '', 'p_gugun_cd': '', 'p_store_nm': None, 'p_theme_cd': None, 'p_wireless_yn': None, 'p_smoking_yn': None, 'p_book_yn': None, 'p_music_yn': None, 'p_terrace_yn': None, 'p_table_yn': None, 'p_takeout_yn': None, 'p_parking_yn': None, 'p_dollar_assent': None, 'p_card_recharge': None, 'p_subway_yn': None, 'stb_store_file_renew': None, 'stb_store_theme_renew': None, 'stb_store_time_renew': None, 'stb_store_lsm': None, 's_code': '1509', 's_name': '역삼아레나빌딩', 'tel': '1522-3232', 'fax': '02-568-3763', 'sido_code': '01', 'sido_name': '서울', 'gugun_code': '0101', 'gugun_name': '강남구', 'addr': '서울특별시 강남구 역삼동 721-13 아레나빌딩', 'park_info': None, 'new_state': None, 'theme_state': 'T05@T08@T16@T17@T20@T21@T30@@T52@P80@P90', 'new_bool'

In [3]:
# pandas.io.json 모듈의 json_normalize() 함수로 json 타입의 데이터가 변환된 딕셔너리를 판다스 데이터프레임으로 변환한다.
# json_normalize(딕셔너리, '데이터프레임으로 변환할 데이터가 할당된 딕셔너리의 key')
starbucks_df = json_normalize(starbucks, 'list')
print(type(starbucks_df)) # <class 'pandas.core.frame.DataFrame'>
print(len(starbucks_df))
print(starbucks_df.columns)

<class 'pandas.core.frame.DataFrame'>
599
Index(['seq', 'sido_cd', 'sido_nm', 'gugun_cd', 'gugun_nm', 'code_order',
       'view_yn', 'store_num', 'sido', 'gugun',
       ...
       't22', 't21', 'p90', 't05', 't30', 't36', 't27', 't29', 't43', 't48'],
      dtype='object', length=129)


In [4]:
starbucks_df

seq sido_cd sido_nm gugun_cd gugun_nm code_order view_yn store_num  sido  \
0      0    None    None     None     None       None    None      None  None   
1      0    None    None     None     None       None    None      None  None   
2      0    None    None     None     None       None    None      None  None   
3      0    None    None     None     None       None    None      None  None   
4      0    None    None     None     None       None    None      None  None   
..   ...     ...     ...      ...      ...        ...     ...       ...   ...   
594    0    None    None     None     None       None    None      None  None   
595    0    None    None     None     None       None    None      None  None   
596    0    None    None     None     None       None    None      None  None   
597    0    None    None     None     None       None    None      None  None   
598    0    None    None     None     None       None    None      None  None   

    gugun  ... t22 t21  p90 t05 t30 t36 t27 t29 t43 t48  
0    None  ...   0   0    0   0   0   0   0   0   0   0  
1    None  ...   0   0    0   0   0   0   0   0   0   0  
2    None  ...   0   0    0   0   0   0   0   0   0   0  
3    None  ...   0   0    0   0   0   0   0   0   0   0  
4    None  ...   0   0    0   0   0   0   0   0   0   0  
..    ...  ...  ..  ..  ...  ..  ..  ..  ..  ..  ..  ..  
594  None  ...   0   0    0   0   0   0   0   0   0   0  
595  None  ...   0   0    0   0   0   0   0   0   0   0  
596  None  ...   0   0    0   0   0   0   0   0   0   0  
597  None  ...   0   0    0   0   0   0   0   0   0   0  
598  None  ...   0   0    0   0   0   0   0   0   0   0  

[599 rows x 129 columns]

In [5]:
# 데이터프레임으로 변환하니 서울에 있는 스타벅스 지점은 599개고 각 지점당 129개의 컬럼으로 정보를 표시하고 있다.
# 작업에 필요한 컬럼 몇 가지를 선택해서 지도에 마커를 표시할 때 사용할 데이터가 저장된 데이터프레임을 만든다.
# s_name       => 지점이름
# sido_code    => 시도코드
# sido_name    => 시도이름
# gugun_code   => 구군코드
# gugun_name   => 구군이름
# doro_address => 도로명주소
# lat          => 위도
# lot          => 경도

In [6]:
# 판다스 데이터프레임에서 특정 컬럼의 데이터를 얻어올 때 얻어올 컬럼이 1개라면 컬럼 이름만 적어도 되지만 얻어올 컬럼이 2개
# 이상일 경우 얻어올 컬럼들을 리스트로 만들어서 얻어와야 한다.
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address',
                                'lat', 'lot']]
starbucks_df_map.head()

s_name sido_code sido_name gugun_code gugun_name  \
0  역삼아레나빌딩        01        서울       0101        강남구   
1   논현역사거리        01        서울       0101        강남구   
2  신사역성일빌딩        01        서울       0101        강남구   
3   국기원사거리        01        서울       0101        강남구   
4  대치재경빌딩R        01        서울       0101        강남구   

                 doro_address         lat          lot  
0     서울특별시 강남구 언주로 425 (역삼동)   37.501087   127.043069  
1    서울특별시 강남구 강남대로 538 (논현동)   37.510178   127.022223  
2    서울특별시 강남구 강남대로 584 (논현동)  37.5139309  127.0206057  
3    서울특별시 강남구 테헤란로 125 (역삼동)   37.499517   127.031495  
4  서울특별시 강남구 남부순환로 2947 (대치동)   37.494668   127.062583

In [7]:
# dtypes 속성으로 판다스 데이터프레임을 구성하는 컬럼들의 자료형을 확인할 수 있다.
# 판다스는 문자열 데이터 타입을 object라 부른다.
starbucks_df_map.dtypes

s_name          object
sido_code       object
sido_name       object
gugun_code      object
gugun_name      object
doro_address    object
lat             object
lot             object
dtype: object

In [8]:
# info() 메소드를 사용해도 데이터프레임을 구성하는 컬럼들의 자료형을 확인할 수 있다.
starbucks_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 599 entries, 0 to 598
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   s_name        599 non-null    object
 1   sido_code     599 non-null    object
 2   sido_name     599 non-null    object
 3   gugun_code    599 non-null    object
 4   gugun_name    599 non-null    object
 5   doro_address  599 non-null    object
 6   lat           599 non-null    object
 7   lot           599 non-null    object
dtypes: object(8)
memory usage: 37.6+ KB


In [9]:
# astype() 메소드로 위도, 경도의 데이터 타입을 object에서 float로 변환한다.
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)
starbucks_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 599 entries, 0 to 598
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   s_name        599 non-null    object 
 1   sido_code     599 non-null    object 
 2   sido_name     599 non-null    object 
 3   gugun_code    599 non-null    object 
 4   gugun_name    599 non-null    object 
 5   doro_address  599 non-null    object 
 6   lat           599 non-null    float64
 7   lot           599 non-null    float64
dtypes: float64(2), object(6)
memory usage: 37.6+ KB


In [10]:
# 종각점
starbucks_df_map[starbucks_df_map['s_name'] == '종각']

s_name sido_code sido_name gugun_code gugun_name            doro_address  \
439     종각        01        서울       0118        종로구  서울특별시 종로구 종로 64 (종로2가)   

           lat         lot  
439  37.569918  126.984528

In [11]:
# 종로관철점
starbucks_df_map[starbucks_df_map['s_name'] == '종로관철']

s_name sido_code sido_name gugun_code gugun_name  \
441   종로관철        01        서울       0118        종로구   

                     doro_address        lat         lot  
441  서울특별시 종로구 종로12길 21, 2층 (관철동)  37.569058  126.986013

In [12]:
# 종로구청점
starbucks_df_map[starbucks_df_map['s_name'] == '종로구청']

s_name sido_code sido_name gugun_code gugun_name            doro_address  \
426   종로구청        01        서울       0118        종로구  서울특별시 종로구 삼봉로 71 (수송동)   

           lat         lot  
426  37.572662  126.981138

In [13]:
starbucksMap = folium.Map(location=[37.5697987, 126.9837167], zoom_start=17)
popup = folium.Popup('종각점', max_width=300)
folium.Marker(location=[37.569918, 126.984528], popup=popup).add_to(starbucksMap)
popup = folium.Popup('종로관철점', max_width=300)
folium.Marker(location=[37.569058, 126.986013], popup=popup).add_to(starbucksMap)
popup = folium.Popup('종로구청점', max_width=300)
folium.Marker(location=[37.572662, 126.981138], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap1.html')
starbucksMap

In [14]:
# 서울특별시에 위치한 스타벅스 전 지점의 위치를 지도위에 표시한다.
# 지도를 작성할 때 지도의 중심으로 설정할 위치가 애매할 경우 지도위에 표시할 모든 스타벅스 지점의 위도와 경도의 평균을
# 중심으로 하는 지도를 만들어 사용하면 된다.
# 판다스 데이터프레임에 저장된 데이터의 평균은 mean() 메소드를 사용해서 계산한다.
starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=12)
# iterrows() 메소드는 판다스 데이터프레임에 저장된 인덱스와 데이터를 리턴한다.
for index, data in starbucks_df_map.iterrows():
    # print(index, data)
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap2.html')
starbucksMap

In [15]:
# 서울특별시 종로구 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '',
    'p_gugun_cd': '0118',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
starbucks_df = json_normalize(starbucks, 'list')
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address', 'lat', 'lot']]
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)

starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=14)
for index, data in starbucks_df_map.iterrows():
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap3.html')
starbucksMap

In [16]:
# 경기도 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '08',
    'p_gugun_cd': '',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
starbucks_df = json_normalize(starbucks, 'list')
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address', 'lat', 'lot']]
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)

starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=10)
for index, data in starbucks_df_map.iterrows():
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap4.html')
starbucksMap

In [17]:
# 제주도 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '16',
    'p_gugun_cd': '',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
starbucks_df = json_normalize(starbucks, 'list')
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address', 'lat', 'lot']]
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)

starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=11)
for index, data in starbucks_df_map.iterrows():
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap5.html')
starbucksMap

In [18]:
# 전국 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '',
    'p_gugun_cd': '',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
starbucks_df = json_normalize(starbucks, 'list')
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address', 'lat', 'lot']]
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)

starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=8)
for index, data in starbucks_df_map.iterrows():
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap6.html')
starbucksMap

In [19]:
# 전국 스타벅스 전 지점
targetSite = 'https://www.starbucks.co.kr/store/getStore.do?r=0B2S7YFEO8'
req = requests.post(targetSite, data={
    'ins_lat': 37.5717888,
    'ins_lng': 126.9661696,
    'p_sido_cd': '',
    'p_gugun_cd': '0821',
    'in_biz_cd': '',
    'iend': 2000,
    'set_date':  ''
})
starbucks = req.json()
starbucks_df = json_normalize(starbucks, 'list')
starbucks_df_map = starbucks_df[['s_name', 'sido_code', 'sido_name', 'gugun_code', 'gugun_name', 'doro_address', 'lat', 'lot']]
starbucks_df_map['lat'] = starbucks_df_map['lat'].astype(float)
starbucks_df_map['lot'] = starbucks_df_map['lot'].astype(float)

starbucksMap = folium.Map(location=[starbucks_df_map['lat'].mean(), starbucks_df_map['lot'].mean()], zoom_start=12)
for index, data in starbucks_df_map.iterrows():
    popup = folium.Popup('{}. {}: {}'.format(index + 1, data['s_name'], data['doro_address']), max_width=300)
    folium.Marker(location=[data['lat'], data['lot']], popup=popup).add_to(starbucksMap)
starbucksMap.save('./starMap7.html')
starbucksMap